In [1]:
import pandas as pd
import time as time
time.time()

1671657769.8232923

## Initialize spark

In [2]:
# find spark
import findspark
findspark.init()

# override cloudpickle in order for reading to work
import cloudpickle
import pyspark.serializers
pyspark.serializers.cloudpickle = cloudpickle
import pyspark.sql.functions as f
from pyspark.ml.feature import Tokenizer, HashingTF, IDF, CountVectorizer
from pyspark.mllib.linalg import SparseVector, DenseVector
from pyspark.mllib.linalg import Vector

In [3]:
# start session
from pyspark.sql import SparkSession
spark = SparkSession.builder.master("local").config("spark.driver.memory", "15g").appName("YeplReviews").getOrCreate()
sc = spark.sparkContext
df = spark.read.json("hdfs://localhost:9000/test/yelp_academic_dataset_review.json")
df = df[["stars", "text"]]
df = df.withColumnRenamed("stars","stars_feature_label")
df = df.withColumn("text", f.regexp_replace("text",r"[\r\n\(\)\.\,\!\?\[\]\/\\\"]"," "))
# add an index column
df = df.withColumn('index', f.monotonically_increasing_id())

# sort ascending and take first 100 rows for df1
df = df.sort('index').limit(100000)
df.show(5, False)

+-------------------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+-----+
|stars_feature_label|text                                                                                                                     

In [4]:
print((df.count(), len(df.columns)))
df.printSchema()

(100000, 3)
root
 |-- stars_feature_label: double (nullable = true)
 |-- text: string (nullable = true)
 |-- index: long (nullable = false)



In [5]:
tokenizer = Tokenizer()
tokenizer.setInputCol('text').setOutputCol('words')
df = tokenizer.transform(df)
df.show(5, False)

+-------------------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+-----+-----------------------------------------------------------------------------------------------------------------------------------------------

In [6]:
cv = CountVectorizer()
cvModel = cv.setInputCol("words").setOutputCol("features").fit(df)
counted = cvModel.transform(df)
counted.head()

Row(stars_feature_label=3.0, text="If you decide to eat here  just be aware it is going to take about 2 hours from beginning to end  We have tried it multiple times  because I want to like it  I have been to it's other locations in NJ and never had a bad experience    The food is good  but it takes a very long time to come out  The waitstaff is very young  but usually pleasant  We have just had too many experiences where we spent way too long waiting  We usually opt for another diner or restaurant on the weekends  in order to be done quicker ", index=0, words=['if', 'you', 'decide', 'to', 'eat', 'here', '', 'just', 'be', 'aware', 'it', 'is', 'going', 'to', 'take', 'about', '2', 'hours', 'from', 'beginning', 'to', 'end', '', 'we', 'have', 'tried', 'it', 'multiple', 'times', '', 'because', 'i', 'want', 'to', 'like', 'it', '', 'i', 'have', 'been', 'to', "it's", 'other', 'locations', 'in', 'nj', 'and', 'never', 'had', 'a', 'bad', 'experience', '', '', '', 'the', 'food', 'is', 'good', '', '

In [7]:
from pyspark.sql.types import ArrayType, StringType
from pyspark.sql.functions import udf
from pyspark.sql.types import *
schema = StructType([
    StructField("stars_feature_label", DecimalType(), False),
    StructField("dict", MapType(StringType(),DecimalType()), False)
])

def indices_to_terms(vocabulary):
    def indices_to_terms(xs):
        sv = xs
        mydict = {}
        for i in list(sv.indices):
            print(i)
            mydict[vocabulary[int(i)]] = int(sv[int(i)])
        return mydict
    return udf(indices_to_terms, MapType(StringType(),IntegerType()))

df2 = counted.withColumn("result_feature", indices_to_terms(cvModel.vocabulary)("features"))
df2.show(5, False)

+-------------------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------+-----+-----------------------------------------------------------------------------------------------------------------------------------------------

In [8]:
time.time()

1671658191.3922956

In [9]:
from pyspark.sql.functions import explode,map_keys,col
keysDF = df2.select(explode(map_keys(df2.result_feature))).distinct()
keysList = keysDF.rdd.map(lambda x:x[0]).collect()
keyCols = list(map(lambda x: col("result_feature").getItem(x).alias(str(x)), keysList))
df = df2.select(df2.stars_feature_label, *keyCols)
df.head()

Py4JJavaError: An error occurred while calling o294671.collectToPython.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 0 in stage 23.0 failed 1 times, most recent failure: Lost task 0.0 in stage 23.0 (TID 370) (DESKTOP-6CVKDOI.mshome.net executor driver): java.net.SocketException: Connection reset by peer: socket write error
	at java.net.SocketOutputStream.socketWrite0(Native Method)
	at java.net.SocketOutputStream.socketWrite(SocketOutputStream.java:111)
	at java.net.SocketOutputStream.write(SocketOutputStream.java:155)
	at java.io.BufferedOutputStream.write(BufferedOutputStream.java:122)
	at java.io.DataOutputStream.write(DataOutputStream.java:107)
	at java.io.FilterOutputStream.write(FilterOutputStream.java:97)
	at org.apache.spark.api.python.PythonRDD$.write$1(PythonRDD.scala:295)
	at org.apache.spark.api.python.PythonRDD$.$anonfun$writeIteratorToStream$1(PythonRDD.scala:307)
	at org.apache.spark.api.python.PythonRDD$.$anonfun$writeIteratorToStre

In [10]:
df = df.na.fill(0)

In [11]:
df.write.option("header", True).csv("../output/something")

Py4JJavaError: An error occurred while calling o294677.csv.
: org.apache.spark.SparkException: Job aborted.
	at org.apache.spark.sql.errors.QueryExecutionErrors$.jobAbortedError(QueryExecutionErrors.scala:651)
	at org.apache.spark.sql.execution.datasources.FileFormatWriter$.write(FileFormatWriter.scala:278)
	at org.apache.spark.sql.execution.datasources.InsertIntoHadoopFsRelationCommand.run(InsertIntoHadoopFsRelationCommand.scala:186)
	at org.apache.spark.sql.execution.command.DataWritingCommandExec.sideEffectResult$lzycompute(commands.scala:113)
	at org.apache.spark.sql.execution.command.DataWritingCommandExec.sideEffectResult(commands.scala:111)
	at org.apache.spark.sql.execution.command.DataWritingCommandExec.executeCollect(commands.scala:125)
	at org.apache.spark.sql.execution.QueryExecution$$anonfun$eagerlyExecuteCommands$1.$anonfun$applyOrElse$1(QueryExecution.scala:98)
	at org.apache.spark.sql.execution.SQLExecution$.$anonfun$withNewExecutionId$6(SQLExecution.scala:109)

In [ ]:
df.head()

In [12]:
print((df.count(), len(df.columns)))
df.printSchema()

(100000, 98171)
root
 |-- stars_feature_label: double (nullable = false)
 |-- online: integer (nullable = true)
 |-- some: integer (nullable = true)
 |-- still: integer (nullable = true)
 |-- strawberry: integer (nullable = true)
 |-- entrée: integer (nullable = true)
 |-- few: integer (nullable = true)
 |-- transaction: integer (nullable = true)
 |-- those: integer (nullable = true)
 |-- traveling: integer (nullable = true)
 |-- art: integer (nullable = true)
 |-- hope: integer (nullable = true)
 |-- muffalata: integer (nullable = true)
 |-- rabe: integer (nullable = true)
 |-- earl: integer (nullable = true)
 |-- monte: integer (nullable = true)
 |-- everyday: integer (nullable = true)
 |-- standards: integer (nullable = true)
 |-- randomly: integer (nullable = true)
 |-- priority: integer (nullable = true)
 |-- brands: integer (nullable = true)
 |-- trail: integer (nullable = true)
 |-- waters: integer (nullable = true)
 |-- jewelry: integer (nullable = true)
 |-- biting: integer (n